In [9]:
import numpy as np
import time
from memory_profiler import memory_usage

np.random.seed(42)

def generate_random_matrix(n):
    return np.random.randint(1, 10, (n, n)).tolist()

def matmul(A, B):
    result = []
    for i in range(len(A)):
        row = []
        for j in range(len(B[0])):
            row.append(sum(A[i][k] * B[k][j] for k in range(len(A[0]))))
        result.append(row)
    return result

def transpose(A):
    return [list(row) for row in zip(*A)]

def subtract(A, B):
    return [[A[i][j] - B[i][j] for j in range(len(A[0]))] for i in range(len(A))]

def inverse_2x2(A):
    if len(A) == 1 and len(A[0]) == 1:
        if abs(A[0][0]) < 1e-10:
            raise ValueError("Matrix is singular")
        return [[1 / A[0][0]]]
    
    if len(A) != 2 or len(A[0]) != 2:
        raise ValueError("inverse_2x2 called with non-2x2 matrix")
    
    det = A[0][0]*A[1][1] - A[0][1]*A[1][0]
    if abs(det) < 1e-10:
        raise ValueError("Matrix is singular")
    
    return [[A[1][1]/det, -A[0][1]/det],
            [-A[1][0]/det, A[0][0]/det]]

def is_singular(A):
    A_np = np.array(A)
    det = np.linalg.det(A_np)
    return abs(det) < 1e-10

# The improved inverse_matrix function using Numpy for stability
def inverse_matrix(A):
    if is_singular(A):
        raise ValueError("Matrix is singular and cannot be inverted")
    
    n = len(A)
    if n <= 2:
        return inverse_2x2(A)
    
    # For larger matrices, we'll use a more stable approach
    # Convert to numpy for the actual inversion operation
    A_np = np.array(A, dtype=float)
    A_inv_np = np.linalg.inv(A_np)
    
    # Convert back to list format to maintain consistency with the rest of the code
    A_inv = A_inv_np.tolist()
    return A_inv

def compute_error(A, A_inv):
    A_np = np.array(A)
    A_inv_np = np.array(A_inv)
    identity = np.eye(len(A_np))
    return np.linalg.norm(A_np @ A_inv_np - identity)

def wrapper(func, *args):
    return func(*args)

if __name__ == '__main__':
    matrix_sizes = [3, 5, 10, 100, 1000]
    
    for size in matrix_sizes:
        print(f"\nSize {size}x{size}")
        
        A = generate_random_matrix(size)
        cond_number = np.linalg.cond(np.array(A))
        
        start_time = time.time()
        mem_usage, A_inv = memory_usage((wrapper, (inverse_matrix, A)), retval=True, max_iterations=1)
        end_time = time.time()
        
        execution_time = end_time - start_time
        peak_memory = max(mem_usage) - min(mem_usage)
        error = compute_error(A, A_inv)
        
        print(f"Condition number: {cond_number:.2e}")
        print(f"Execution time: {execution_time:.6f} seconds")
        print(f"Peak memory usage: {peak_memory:.6f} MiB")
        print(f"Error ||AA⁻¹ - I||: {error:.2e}")
        print(f"Inverse matrix {size}x{size}:")
        for row in A_inv:
            formatted_row = [round(float(val), 4) for val in row]
            print(formatted_row)


Size 3x3
Condition number: 1.33e+02
Execution time: 0.356589 seconds
Peak memory usage: 1.343750 MiB
Error ||AA⁻¹ - I||: 5.12e-15
Inverse matrix 3x3:
[-1.0, -4.0, 4.0]
[0.3636, 1.9091, -1.7273]
[0.8182, 2.5455, -2.6364]

Size 5x5
Condition number: 1.33e+02
Execution time: 0.286292 seconds
Peak memory usage: 2.390625 MiB
Error ||AA⁻¹ - I||: 4.93e-15
Inverse matrix 5x5:
[1.572, -2.6965, 2.7315, -1.2763, -0.3268]
[0.3599, -0.4825, 0.4076, -0.1313, -0.1342]
[-0.7043, 1.463, -1.3327, 0.5272, 0.1167]
[-0.4202, 0.5525, -0.5272, 0.356, 0.0973]
[-0.2121, 0.214, -0.3239, 0.1449, 0.1926]

Size 10x10
Condition number: 3.87e+02
Execution time: 0.191929 seconds
Peak memory usage: 0.437500 MiB
Error ||AA⁻¹ - I||: 1.67e-14
Inverse matrix 10x10:
[0.3873, -0.3082, 0.4312, -0.4569, -0.1754, 0.4782, 0.1092, -0.0278, -0.605, 0.1499]
[0.9979, -1.1571, 1.4432, -1.2295, -0.5993, 1.2764, -0.0445, 0.4997, -1.962, 0.5202]
[-0.8825, 0.9559, -1.1095, 0.9117, 0.5141, -0.9574, 0.094, -0.2876, 1.3895, -0.3565]
[0.50

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/numpy/linalg/_linalg.py:2432: RuntimeWarning: overflow encountered in det
  r = _umath_linalg.det(a, signature=signature)


Condition number: 1.09e+05
Execution time: 0.395096 seconds
Peak memory usage: 91.937500 MiB
Error ||AA⁻¹ - I||: 3.44e-11
Inverse matrix 1000x1000:
[-0.085, 0.0305, -0.0162, -0.0012, -0.0546, -0.0769, -0.0186, 0.02, 0.0077, 0.0059, 0.0567, 0.0103, 0.0055, 0.0556, 0.0189, 0.021, 0.0656, 0.0152, -0.0636, 0.0264, 0.0183, -0.0611, 0.002, 0.0265, -0.0, 0.0442, 0.0444, 0.0109, 0.0246, -0.0974, 0.0429, -0.0222, -0.0767, 0.023, -0.0897, -0.0422, -0.0176, 0.0085, 0.0056, 0.0205, -0.0413, -0.0432, 0.0423, 0.0241, -0.0246, 0.0283, 0.0241, 0.0171, -0.0259, -0.0378, -0.0059, 0.0179, 0.0005, -0.0396, -0.0131, 0.0313, 0.0641, -0.0319, 0.0099, 0.033, -0.0237, 0.0228, -0.0301, 0.024, -0.0134, 0.0269, -0.0546, -0.0191, 0.0119, 0.0436, -0.0111, 0.0083, -0.0064, -0.018, 0.0209, 0.1075, 0.0147, 0.0461, -0.0381, -0.0187, -0.0274, 0.006, -0.0383, -0.0077, 0.0524, -0.0368, 0.0649, -0.0465, 0.047, 0.0097, -0.0533, -0.047, 0.0072, 0.0113, 0.0552, -0.048, 0.0016, -0.0031, -0.0188, 0.0215, -0.0348, 0.0295, -0.007